[Day 19](https://adventofcode.com/2019/day/19) puzzle input is an IntCode program (mine is [here](puzzle_input/day19.txt)) which will models a sort of beam, and when provided with an x/y co-ordinate will output whether the beam is in effect at that position. Part 1 involves finding the number of positions for x and y in the range 0-49 which are affected by the beam. Part 2 involves figuring out the first 100x100 section which can be wholly contained within the beam (position of the top-left corner).

In [1]:
opcode_add = 1
opcode_mul = 2
opcode_read = 3
opcode_write = 4
opcode_jump_true = 5
opcode_jump_false = 6
opcode_lt = 7
opcode_eq = 8
opcode_rebase = 9

opcode_terminate = 99

mode_position = 0
mode_immediate = 1
mode_relative = 2

class IntCodeCpu:
    def __init__(self, memory_image):
        self.memory = [ x for x in memory_image ] # copy memory image, in case it's reused
        self.stalled = True
        self.input_buffer = None
        self.output_buffer = None
        self.pc = 0
        self.initialise_opcodes()
        self.offset = 0
        self.done = False
        
    def start(self, input_buffer, output_buffer, noun=None, verb=None):
        self.input_buffer = input_buffer
        self.output_buffer = output_buffer

        if noun:
            self.memory[1] = noun
        if verb:
            self.memory[2] = verb
           
        return self.run()
            
            
    def run(self):
        instr = self.memory[self.pc]
        self.stalled = False

        while int(instr) != opcode_terminate and not self.stalled:
            (op, modes) = self.decode_instr(instr)
            self.pc = op(modes)
            instr = self.memory[self.pc]

        return self.memory[0]

    #-HELPERS-----------------------------
    def try_pop_mode(self, modes):
        if len(modes) == 0:
            return 0
    
        return modes.pop()
    
    def resize_memory(self, target_addr):
        self.memory += ([0] * (1 + target_addr - len(self.memory)))
    
    #-DECODE-INSTRUCTIONS-----------------
    def initialise_opcodes(self):
        self.opcodes = {
            opcode_add: self.op_add,
            opcode_mul: self.op_mul,
            opcode_read: self.op_read,
            opcode_write: self.op_write,
            opcode_jump_true: self.op_jump_true,
            opcode_jump_false: self.op_jump_false,
            opcode_lt: self.op_lt,
            opcode_eq: self.op_eq,
            opcode_rebase: self.op_rebase
        }    
    
    def decode_instr(self, instr):
        instr = str(instr)
        opcode = self.decode_op(instr)
        modes = self.decode_modes(instr)

        if not (opcode in self.opcodes):
            raise Exception(f"Invalid opcode {opcode}")

        return (self.opcodes[opcode], modes)    
    
    def decode_op(self, instr):
        if len(instr) > 2:
            return int(instr[-2:])
        return int(instr)
    
    def decode_modes(self, instr):
        if len(instr) > 2:
            return [ int(d) for d in instr[:-2]]
        return []
    
    #-MICRO-OPS---------------------------
    def uop_read(self, value, mode):
        if mode == mode_position:
            if value >= len(self.memory):
                self.resize_memory(value)        

            return int(self.memory[value])

        elif mode == mode_relative:
            if self.offset + value >= len(self.memory):
                self.resize_memory(self.offset + value)     

            return int(self.memory[self.offset + value])

        elif mode == mode_immediate:
            return int(value)

        else:
            raise Exception("UNKNOWN MODE")

    def uop_write(self, dst, value, mode):
        if mode == mode_position:
            if dst >= len(self.memory):
                self.resize_memory(dst)
            self.memory[dst] = value

        elif mode == mode_relative:
            if self.offset + dst >= len(self.memory):
                self.resize_memory(self.offset + dst)     

            self.memory[self.offset + dst] = value

        elif mode == mode_immediate:
            raise Exception(f"cannot write {value} to literal {dst}")


    def uop_cond_jump(self, modes, cond):
        param_mode = self.try_pop_mode(modes)
        param_raw = int(self.memory[self.pc + 1])
        param = self.uop_read(param_raw, param_mode)

        dest_mode = self.try_pop_mode(modes)
        dest_raw = int(self.memory[self.pc + 2])
        dest = self.uop_read(dest_raw, dest_mode)

        if cond(param):
            return dest

        return self.pc + 3

    def uop_cmp(self, modes, cmp):

        param0_mode = self.try_pop_mode(modes)
        param0_raw = int(self.memory[self.pc + 1])
        param0 = self.uop_read(param0_raw, param0_mode)

        param1_mode = self.try_pop_mode(modes)
        param1_raw = int(self.memory[self.pc + 2])
        param1 = self.uop_read(param1_raw, param1_mode)

        dest_mode = self.try_pop_mode(modes)
        dest = int(self.memory[self.pc + 3])

        if cmp(param0, param1):
            self.uop_write(dest, 1, dest_mode)
        else:
            self.uop_write(dest, 0, dest_mode)

        return self.pc + 4
        
    
    #-OPCODES-----------------------------
    def op_add(self, modes):
        arg0_mode = self.try_pop_mode(modes)
        arg1_mode = self.try_pop_mode(modes)
        dest_mode = self.try_pop_mode(modes)

        arg0_raw = int(self.memory[self.pc + 1])
        arg1_raw = int(self.memory[self.pc + 2])
        dest = int(self.memory[self.pc + 3])

        arg0 = self.uop_read(arg0_raw, arg0_mode)
        arg1 = self.uop_read(arg1_raw, arg1_mode)

        self.uop_write(dest, str(int(arg0) + int(arg1)), dest_mode)
        return self.pc + 4

    def op_mul(self, modes):
        arg0_mode = self.try_pop_mode(modes)
        arg1_mode = self.try_pop_mode(modes)
        dest_mode = self.try_pop_mode(modes)

        arg0_raw = int(self.memory[self.pc + 1])
        arg1_raw = int(self.memory[self.pc + 2])
        dest = int(self.memory[self.pc + 3])

        arg0 = self.uop_read(arg0_raw, arg0_mode)
        arg1 = self.uop_read(arg1_raw, arg1_mode)

        self.uop_write(dest, str(int(arg0) * int(arg1)), dest_mode)    
        return self.pc + 4


    def op_read(self, modes):
        dest_mode = self.try_pop_mode(modes)
        dest = int(self.memory[self.pc + 1])
        
        # if the input buffer is empty, we should "stall" and 
        # resume later
        if not self.input_buffer:
            self.stalled = True
            return self.pc
        
        val = self.input_buffer.pop()

        self.uop_write(dest, str(val), dest_mode)

        return self.pc + 2

    def op_write(self, modes):
        src_mode = self.try_pop_mode(modes)
        src_raw = int(self.memory[self.pc + 1])
        src = self.uop_read(src_raw, src_mode)

        self.output_buffer.append(src)

        return self.pc + 2

    def op_jump_true(self, modes):
        return self.uop_cond_jump(modes, lambda x: x != 0)


    def op_jump_false(self, modes):
        return self.uop_cond_jump(modes, lambda x: x == 0)

    def op_lt(self, modes):
        return self.uop_cmp(modes, lambda x, y: x < y)

    def op_eq(self, modes):
        return self.uop_cmp(modes, lambda x, y: x == y)

    def op_rebase(self, modes):    
        param_mode = self.try_pop_mode(modes)
        param_raw = int(self.memory[self.pc + 1])
        param = self.uop_read(param_raw, param_mode)

        self.offset += param

        return self.pc + 2

In [2]:
raw_code = open("puzzle_input/day19.txt", "r").read()
code = raw_code.split(",")

points_affected = 0
output = []
output_buffer = []

for row in range(0,50):
    current_row = []
    for col in range(0, 50):
        cpu = IntCodeCpu(code)
        cpu.start([row, col], output_buffer)
        assert 1 == len(output_buffer)
        points_affected += output_buffer[0]
        output_buffer = []
    output.append(current_row)

print(points_affected)

217


In [3]:
def in_beam(row, col):
    # is it necessary to create new cpu each time?
    cpu = IntCodeCpu(code)
    output_buffer = []
    input_buffer = [row, col]
    cpu.start(input_buffer, output_buffer)
    assert 1 == len(output_buffer)
    return output_buffer[0] == 1

def beam_at_row(row, start_col):
    beam_start = start_col
    beam_width = 0
    col = start_col
    
    # mine has an empty area in rows
    # 1 and 2 so use precomputed values
    # yes this is yet another horrible hack
    if row < 3:
        return [
            (0,1),
            (0,0),
            (0,0)
        ][row]
    
    # seek to the beam start
    while not in_beam(row, col):
        beam_start += 1
        col += 1
    
    # continue to beam end
    while in_beam(row, col):
        beam_width += 1
        col += 1
    
    return (beam_start, beam_width)

    
def beam_can_contain_cube(beam_data, cube_size):
    current_beam_index = len(beam_data) - 1
    current_beam_start, current_beam_width = beam_data[current_beam_index]
    
    # so we need to check if:
    # 0. there have been at least enough beams (we'll be looking back in the beam_data by cube_size)
    if current_beam_index - cube_size < 0:
        return False
    
    # 1. the beam width starting at the current line < cube_size
    if current_beam_width < cube_size:
        return False
    
    # 2. the same point at line (current_beam_index - cube_size) is in beam
    start_beam_index = current_beam_index - (cube_size - 1)
    start_beam_start, start_beam_width = beam_data[start_beam_index]
    if current_beam_start >= start_beam_start + start_beam_width:
        return False
    
    # 3. there's enough beam at that ^^^ line afterwards to contain the beam
    if current_beam_start + cube_size > start_beam_start + start_beam_width:
        return False
    
    return True
    
#################
target_cube = 100
    
# seed our beam with a few rows to get going
beam = [ beam_at_row(n, 0) for n in range(0, 20) ]    
current_beam = len(beam)
start_col = 2

while not(beam_can_contain_cube(beam, target_cube)):
    current = beam_at_row(current_beam, start_col-1)
    start_col, current_size = current
    beam.append(current)
    current_beam += 1
    
cube_end_row = current_beam - 1
cube_start_row = cube_end_row - (target_cube - 1)
current_beam_start_col, current_beam_width = beam[-1]
print((current_beam_start_col * 10000) + cube_start_row)

6840937
